# Service 1

In [1]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 386.6/386.6 kB 7.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 231.9/231.9 kB 16.5 MB/s eta 0:00:00


In [2]:
import pandas as pd
import optuna
import numpy as np
from lightgbm import LGBMRegressor
from sklearn.model_selection import train_test_split
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import mean_squared_error

# Load the dataset
df = pd.read_csv("Service1.csv")

# Define input features and target outputs
X = df[['latency_ms', 'cpu_usage_pct', 'memory_usage_pct']]
y = df[['cpu_allocated', 'memory_allocated']]

# Train-validation-test split: 70% train, 15% val, 15% test
X_train_full, X_temp, y_train_full, y_temp = train_test_split(X, y, test_size=0.30, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.50, random_state=42)

# Define Optuna objective function for LightGBM
def objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 200),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'subsample': trial.suggest_float('subsample', 0.6, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
    }

    model = MultiOutputRegressor(LGBMRegressor(**params, random_state=42))
    model.fit(X_train_full, y_train_full)
    preds = model.predict(X_val)
    mse = mean_squared_error(y_val, preds)
    return mse

# Run Optuna study
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=30)
best_params = study.best_params
print("Best Parameters:", best_params)

# Retrain model on train + validation data
X_train_combined = pd.concat([X_train_full, X_val])
y_train_combined = pd.concat([y_train_full, y_val])

final_model = MultiOutputRegressor(LGBMRegressor(**best_params, random_state=42))
final_model.fit(X_train_combined, y_train_combined)

# Evaluate on test set
predictions = final_model.predict(X_test)
mse = mean_squared_error(y_test, predictions)
rmse = np.sqrt(mse)
print(f"\nTest MSE: {mse:.4f}")
print(f"Test RMSE: {rmse:.4f}")

# Example: Predicting resource allocation from sample input
sample = pd.DataFrame([[300, 40, 70]], columns=['latency_ms', 'cpu_usage_pct', 'memory_usage_pct'])
predicted_allocation = final_model.predict(sample)
print(f"\nSample Input: {sample.to_dict(orient='records')[0]}")
print(f"Predicted CPU, Memory Allocation: {predicted_allocation[0]}")


[I 2025-05-05 05:38:51,938] A new study created in memory with name: no-name-5c076734-9e59-4cd5-8505-d7e4a41b8e66


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000498 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 3
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

[I 2025-05-05 05:38:52,254] Trial 0 finished with value: 1.7177696557370241 and parameters: {'n_estimators': 129, 'learning_rate': 0.12469141324930932, 'num_leaves': 151, 'max_depth': 12, 'subsample': 0.6517581912182749, 'colsample_bytree': 0.9093800810455224, 'reg_alpha': 0.6689204444977971, 'reg_lambda': 0.9377964892645138}. Best is trial 0 with value: 1.7177696557370241.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000322 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 3
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

[I 2025-05-05 05:38:52,526] Trial 1 finished with value: 1.6145471149111508 and parameters: {'n_estimators': 264, 'learning_rate': 0.1025606175131234, 'num_leaves': 176, 'max_depth': 5, 'subsample': 0.7827861309987254, 'colsample_bytree': 0.871992203977165, 'reg_alpha': 0.9612907981045514, 'reg_lambda': 0.5919923665149079}. Best is trial 1 with value: 1.6145471149111508.


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000241 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 3
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

[I 2025-05-05 05:39:18,113] Trial 28 finished with value: 1.80256075776157 and parameters: {'n_estimators': 998, 'learning_rate': 0.1901517658975003, 'num_leaves': 111, 'max_depth': 11, 'subsample': 0.9967552742482897, 'colsample_bytree': 0.6280521324225554, 'reg_alpha': 0.7660854821093089, 'reg_lambda': 0.43091810393838215}. Best is trial 11 with value: 1.5114543549837627.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000412 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 3
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

[I 2025-05-05 05:39:18,692] Trial 29 finished with value: 1.5777523577470949 and parameters: {'n_estimators': 115, 'learning_rate': 0.086068802861907, 'num_leaves': 130, 'max_depth': 15, 'subsample': 0.6164027019067573, 'colsample_bytree': 0.6038072145781512, 'reg_alpha': 0.8937773345581335, 'reg_lambda': 0.9206667080956288}. Best is trial 11 with value: 1.5114543549837627.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Best Parameters: {'n_esti

# Service 2

In [3]:
import pandas as pd
import optuna
import numpy as np
from lightgbm import LGBMRegressor
from sklearn.model_selection import train_test_split
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import mean_squared_error

# Load the dataset
df = pd.read_csv("Service2.csv")

# Define input features and target outputs
X = df[['latency_ms', 'cpu_usage_pct', 'memory_usage_pct']]
y = df[['cpu_allocated', 'memory_allocated']]

# Train-validation-test split: 70% train, 15% val, 15% test
X_train_full, X_temp, y_train_full, y_temp = train_test_split(X, y, test_size=0.30, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.50, random_state=42)

# Define Optuna objective function for LightGBM
def objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 200),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'subsample': trial.suggest_float('subsample', 0.6, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
    }

    model = MultiOutputRegressor(LGBMRegressor(**params, random_state=42))
    model.fit(X_train_full, y_train_full)
    preds = model.predict(X_val)
    mse = mean_squared_error(y_val, preds)
    return mse

# Run Optuna study
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=30)
best_params = study.best_params
print("Best Parameters:", best_params)

# Retrain model on train + validation data
X_train_combined = pd.concat([X_train_full, X_val])
y_train_combined = pd.concat([y_train_full, y_val])

final_model = MultiOutputRegressor(LGBMRegressor(**best_params, random_state=42))
final_model.fit(X_train_combined, y_train_combined)

# Evaluate on test set
predictions = final_model.predict(X_test)
mse = mean_squared_error(y_test, predictions)
rmse = np.sqrt(mse)
print(f"\nTest MSE: {mse:.4f}")
print(f"Test RMSE: {rmse:.4f}")

# Example: Predicting resource allocation from sample input
sample = pd.DataFrame([[300, 40, 70]], columns=['latency_ms', 'cpu_usage_pct', 'memory_usage_pct'])
predicted_allocation = final_model.predict(sample)
print(f"\nSample Input: {sample.to_dict(orient='records')[0]}")
print(f"Predicted CPU, Memory Allocation: {predicted_allocation[0]}")


[I 2025-05-05 05:40:01,993] A new study created in memory with name: no-name-1304044d-542e-4d98-b435-41bc49008555


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000415 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 3
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

[I 2025-05-05 05:40:03,148] Trial 0 finished with value: 1.6038402175753523 and parameters: {'n_estimators': 651, 'learning_rate': 0.1024903636897669, 'num_leaves': 133, 'max_depth': 8, 'subsample': 0.7740722395157427, 'colsample_bytree': 0.6611395345564938, 'reg_alpha': 0.3736421549756912, 'reg_lambda': 0.3917893385381397}. Best is trial 0 with value: 1.6038402175753523.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000264 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 3
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

[I 2025-05-05 05:40:04,180] Trial 1 finished with value: 1.6317392057205726 and parameters: {'n_estimators': 526, 'learning_rate': 0.03993131288373824, 'num_leaves': 85, 'max_depth': 14, 'subsample': 0.9002644272912811, 'colsample_bytree': 0.8427576005405504, 'reg_alpha': 0.8662918988579237, 'reg_lambda': 0.49224597077196985}. Best is trial 0 with value: 1.6038402175753523.


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000274 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 3
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

[I 2025-05-05 05:40:31,735] Trial 28 finished with value: 1.6973739494085103 and parameters: {'n_estimators': 841, 'learning_rate': 0.07685714946537625, 'num_leaves': 38, 'max_depth': 12, 'subsample': 0.7876939042863527, 'colsample_bytree': 0.9625701113339733, 'reg_alpha': 0.915536752884943, 'reg_lambda': 0.7071542504383745}. Best is trial 22 with value: 1.4839847290439914.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000250 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 3
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

[I 2025-05-05 05:40:32,627] Trial 29 finished with value: 1.6950637449446944 and parameters: {'n_estimators': 659, 'learning_rate': 0.10512468950448554, 'num_leaves': 51, 'max_depth': 8, 'subsample': 0.7479230618490877, 'colsample_bytree': 0.9957835523523785, 'reg_alpha': 0.3902098705287469, 'reg_lambda': 0.3727919363769729}. Best is trial 22 with value: 1.4839847290439914.


Best Parameters: {'n_estimators': 714, 'learning_rate': 0.013030796092470518, 'num_leaves': 20, 'max_depth': 11, 'subsample': 0.962722267627185, 'colsample_bytree': 0.999648484033937, 'reg_alpha': 0.8761218124214908, 'reg_lambda': 0.907441918667866}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000488 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 763
[LightGBM] [Info] Number of data points in the train set: 8500, number of used features: 3
[LightGBM] [Info] Start training from score 0.549234
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli